## Install

In [ ]:
# install bark (make sure you have torch>=2 for much faster flash-attention)
!pip install git+https://github.com/suno-ai/bark.git
!pip install openai

In [11]:
from bark import SAMPLE_RATE, generate_audio, preload_models
from IPython.display import Audio

preload_models()

In [12]:
from IPython.display import Audio
import nltk  # we'll use this to split into sentences
import numpy as np

from bark.generation import (
    generate_text_semantic,
    preload_models,
)
from bark.api import (
    semantic_to_waveform,
)

In [13]:
nltk.download('punkt') #additonal nltk package to split sentences

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [14]:
#This cell uses a discord-based free API instead of Chat-GPT. You may use Chat-GPT instead if the API key is available.
import openai

openai.api_key = 'pk-*************************************'
openai.api_base = 'https://api.pawan.krd/v1'

topic="the obstacles in life" #The prompt can be input here, todo - create a GUI for this.
promptfin = "generate a poem about" + topic
response = openai.Completion.create(
  model="pai-001-beta",
  prompt=promptfin,
  temperature=0.7,
  max_tokens=256,
  top_p=1,
  frequency_penalty=0,
  presence_penalty=0,
)

print(response.choices[0].text)


 In life's rich tapestry, woven with strife,
Our path is not always smooth and bright.

Obstacles arise, like shadows cast,
To test our strength, endurance, and flight.

The first one looms, a figure grim,
As big as mountains, vast and wide.
Its name is Fear, it whispers low,
"Turn back now, for danger's inside."

We muster courage, heart pounding loud,
And face this giant, unafraid.
With each step forward, fear recedes,
And we learn that it was but a shade.

Next obstacle appears, a chasm deep,
Between us and our dreams so pure.
Its name is Doubt, a voice so weak,
That questions every move we seek to ensure.

But faith within us burns so bright,
Guiding us across the darkest night.
Step by step, we overcome,
And see that doubt was but a spur.

Then comes the time when resources wane,
And we feel weary, worn, and drained.
I


In [15]:
script = response.choices[0].text
script = script.strip().split("\n")
script = [s.strip() for s in script if s]
script

["In life's rich tapestry, woven with strife,",
 'Our path is not always smooth and bright.',
 'Obstacles arise, like shadows cast,',
 'To test our strength, endurance, and flight.',
 'The first one looms, a figure grim,',
 'As big as mountains, vast and wide.',
 'Its name is Fear, it whispers low,',
 '"Turn back now, for danger\'s inside."',
 'We muster courage, heart pounding loud,',
 'And face this giant, unafraid.',
 'With each step forward, fear recedes,',
 'And we learn that it was but a shade.',
 'Next obstacle appears, a chasm deep,',
 'Between us and our dreams so pure.',
 'Its name is Doubt, a voice so weak,',
 'That questions every move we seek to ensure.',
 'But faith within us burns so bright,',
 'Guiding us across the darkest night.',
 'Step by step, we overcome,',
 'And see that doubt was but a spur.',
 'Then comes the time when resources wane,',
 'And we feel weary, worn, and drained.',
 'I']

In [16]:
#testing just one line, ignore cell and skip ahead to generate the whole piece.
SPEAKER = "v2/en_speaker_9"
audio_array = generate_audio(script[4],history_prompt=SPEAKER)
Audio(audio_array, rate=SAMPLE_RATE)

100%|██████████| 10/10 [00:09<00:00,  1.08it/s]


In [18]:
#generate piece by piece and then join together since the model does not directly allow long generation.
SPEAKER = "v2/en_speaker_9"
silence = np.zeros(int(0.25 * SAMPLE_RATE))  # quarter second of silence

pieces = []
for sentence in script:
    audio_array = generate_audio(sentence, history_prompt=SPEAKER)
    pieces += [audio_array, silence.copy()]


100%|██████████| 3/3 [00:02<00:00,  1.08it/s]


In [26]:

Audio(np.concatenate(pieces), rate=SAMPLE_RATE)


In [28]:
from scipy.io import wavfile
wavfile.write("poem.wav", SAMPLE_RATE, np.concatenate(pieces))